<div align="left">
<img src="https://licensebuttons.net/l/by-nc-sa/3.0/88x31.png" align="right">
<p align="left"><b>Autor: Víctor Sánchez Anguix</b></p>
</div>
<img align="left" width="30%" src="https://www.inf.upv.es/www/etsinf/wp-content/uploads/2017/02/ETSInf_PRINCIPAL_V-horizontal.png"/> <img width="30%" src="https://www.upv.es/perfiles/pas-pdi/imagenes/marca_UPV_principal_negro150.png" align="right"/>


# Optimization: Project I 2023

In this notebook we define the first project for this course. The project constitutes the application of your knowledge about optimization modeling and implementation of those models to a real-world problem that requires a large number of variables and constraints.

First, we will describe the domain where the project is situated. That is, the scenario in which we place ourselves as analysts. After that, we describe the details of the submission.

Remember that for this project you can work in teams of up to 5 students. In fact, teamwork is highly recommended due to the size and complexity of the project.

# Scenario

In this section we will describe in detail both the problem to be solved, as well as some particularities about the organization that you have recently joined.

##Introduction

You have recently been hired as analysts for the analytics department of the *Fire Department of the City of New York*. This department is in charge of managing, both at an strategic and operational level, everything related to the fire emergencies of the city. Therefore, it is one of the city's emergency departments and it plays a very important role in the welfare of the city.

<center>
<img src="https://upload.wikimedia.org/wikipedia/commons/thumb/2/25/Emblem_of_the_New_York_City_Fire_Department.svg/800px-Emblem_of_the_New_York_City_Fire_Department.svg.png" width="30%"/>
</center>

The department is the largest in the United States, and it is also the second largest in the world. Therefore, the complexity of the department's organization is high, and so is the amount of resources to be managed. On the other hand, the tasks performed by this department are varied. Although the most obvious task is fire extinguishing, the city's fire department is also involved in the disposal of chemical and harmful materials, rescue operations, and medical emergencies in the city.

Currently, the fire department serves the five major boroughs that make up New York City:
* Manhattan: the nerve center of New York City, where most of the economic activity takes place and where the most luxurious housing is located.
* Brooklyn: The largest borough in population. In recent years it has become home to many families and young professionals due to the more reasonable prices compared to Manhattan and its vibrant artistic, creative and restaurant atmosphere.
* Bronx: One of the most culturally diverse boroughs in the city, with some of the most affordable housing. In the past it has been considered a problematic borough, but the quality of life has been gradually improving. However, it has not yet reached, on a general level, the safety standards of the other boroughs.
* Queens: This is the largest borough in terms of size. It is also less expensive than Manhattan and is it very well connected to it. However, travel times are longer as it is farther away than Brooklyn.
* Staten Island: This borough is sometimes forgotten because it is far from the rest. However, it also belongs to the city of New York. It is also the least populated of all the large boroughs. It concentrates less economic activity than the other boroughs.

In the following interactive map you can see the 5 major boroughs of New York City, as well as some associated information. Specifically, you can also see the neighborhoods of each of the 5 boroughs, their names, and area by hovering the pointer over the polygon. If you do not see the map correctly, try re-executing the following code snippet.



In [ ]:
import folium
import requests
import json
import geopandas as geo

response = requests.get("https://gitlab.com/drvicsana/cop-proyecto-2023/-/raw/main/nta_shapes.json")
json_response = json.loads(response.text)

map = folium.Map(location=[40.70, -73.94], zoom_start=10, width="50%", tiles="CartoDB positron")

color_maps = {"MN": "orange", "QN": "red", "BK": "green", "BX": "purple", "SI": "pink"}

for polygon in json_response["features"]:
  geo_j = folium.GeoJson(data=polygon, style_function=lambda x: {"fillColor": color_maps[x["properties"]["nta"][0:2]], "weight":1})
  folium.GeoJsonTooltip(["nta", "NTAName", "BoroName", "Shape_Area"]).add_to(geo_j)
  geo_j.add_to(map)
map

At the operational level, the department is organized into companies. A company operates a single type of vehicle and it is specialized in the management of that vehicle and the tools carried on it. For the context of this project, there are 5 types of vehicles and, therefore, 5 types of companies to consider:

* Engine companies: They are in charge of extinguishing fires by means of the vehicle's water tank and the water available through the hydrants on the streets of New York. It has basic medical equipment, ground ladders and some basic tools. There are currently 197 vehicles of this type
  <center>
    <img src="https://upload.wikimedia.org/wikipedia/commons/thumb/1/16/Peter_Stehlik_-_FDNY_Engine_34_-_2012.05.18.jpg/1280px-Peter_Stehlik_-_FDNY_Engine_34_-_2012.05.18.jpg" width="30%"/>
  </center>
* Ladder companies: They are in charge of forced entry, searching for people, ventilation, and tasks that require extensible ladders. There are currently 143 vehicles of this type.
  <center>
    <img src="https://upload.wikimedia.org/wikipedia/commons/thumb/c/ce/Peter_Stehlik_-_FDNY_Ladder_4_-_2012.05.23.jpg/1280px-Peter_Stehlik_-_FDNY_Ladder_4_-_2012.05.23.jpg" width="30%"/>
  </center>
* Rescue companies: These companies are highly specialized in special rescues that are beyond the scope of normal companies. They have vehicles equipped for rope rescues, building collapse rescues, confined space rescues, underground rescues, water rescues, and other scenarios. There are a total of 5 of these vehicles.
<center>
  <img src="https://upload.wikimedia.org/wikipedia/commons/thumb/0/09/Peter_Stehlik_-_FDNY_Rescue_1_-_2012.05.18.JPG/1280px-Peter_Stehlik_-_FDNY_Rescue_1_-_2012.05.18.JPG" width="30%"/>
</center>
* Squad companies: These are hybrid companies that have the attributes of *ladder* and *engine* companies, but also have some tools for rescue and treatment of harmful substances. There are a total of 8 companies.
<center>
  <img src="http://10-75.net/imagesiii/DSC06769%20copy.jpg" width="30%"/>
</center>
* Hazmat companies: These are companies specialized in the treatment of waste and materials harmful to life or the environment. There is only one company of this type.
<center>
  <img src="https://upload.wikimedia.org/wikipedia/commons/thumb/1/17/Peter_Stehlik_-_FDNY_HazMat_1_-_2012.05.23.jpg/1280px-Peter_Stehlik_-_FDNY_HazMat_1_-_2012.05.23.jpg" width="30%"/>
</center>

These companies can be located in one of the 218 infrastructures that can serve as parking for firefighters and their vehicles. These infrastructures, which we will call as *stations*, are distributed throughout the city. The following map shows the distribution of these stations as well as some associated information.

In [ ]:
response = requests.get("https://gitlab.com/drvicsana/cop-proyecto-2023/-/raw/main/located_firehouses.json")
json_response = json.loads(response.text)

map = folium.Map(location=[40.70, -73.94], zoom_start=10, width="50%", tiles="CartoDB positron")

for polygon in json_response["features"]:
  marker = folium.Marker([polygon["geometry"]["coordinates"][1], polygon["geometry"]["coordinates"][0]])
  tooltip = folium.Tooltip("<b>Location</b>: {}<br><b>Capacity</b>: {}".format(polygon["properties"]["FacilityAddress"], polygon["properties"]["capacity"]))
  tooltip.add_to(marker)
  marker.add_to(map)

map

The fire department primarily runs two shifts. The first shift, also known as the night shift, runs from 6 PM until 9 AM. The second shift runs from 9 AM to 6 PM.

The way the shifts work is as follows:
* Shifts start from one of 218 possible stations.
* The vehicle is parked at the assigned station until a new emergency to be covered arises.
* In the case of a new emergency, the firefighters leave with their vehicle to cover the assigned emergency.
* At the end of the emergency, they return to the station where the shift started.
* This process is repeated until the shift ends. In this case, the vehicle can stay at the station of the previous shift or be taken by the staff to a new station.

The city department wishes to optimize the location of these vehicles, as well as the assignment of service to New York neighborhoods.

## Some aspects to consider for the optimization

Emergency services, as is the case of the fire department, are departments that seek both to serve as many people as possible and to do so in the shortest possible time. The former is due to the fact that it is a service for all citizens, so leaving any area uncovered would have significant negative effects on the image of the service. The second is due to the fact that in the case of emergencies, it is advisable to act as quickly as possible to minimize the damage to both the city's infrastructures and human lives.

New York City is comprised of its five major boroughs. Within the city's fire department, there are representatives and chief operating officers for each of the boroughs. They seek to respond to the needs of their stakeholders. The reality is that each of these boroughs is an influence group within the local and operational decisions of the department. Strongly favoring any one of the boroughs in service planning would mean major tensions and internal and external complaints.

In addition, for scarce resources such as squad or rescue companies, it is better not to group them in the same location, since it is interesting that they cover a wide geographic area. If a single borough concentrates all vehicles of the same type, it would again cause tensions within the department and at the city council level. Therefore, it has been suggested that the planning should consider the multi-district nature of New York City. The only exception is the hazmat vehicle, since only one of these resources is available.

In the eyes of the local administrators, it would also seem strange that when a station accommodates more than one vehicle, it contains all vehicles of the same type. This gives a sense of misallocation of available resources since those extra vehicles could be used to increase the area covered by the department.

Also, we should keep in mind that there are different types of emergencies covered by the fire department. That is, any vehicle cannot be used for everything. The frequency of these emergencies can be affected by different factors, both temporal and structural.

At shift change, ambulances should not travel long distances, as this causes a sense of increased work and fatigue for the workers making the trip between stations.







# Available data

To carry out this project you have been given a series of databases to work with. We will now review each of these databases:

The file **barrios.json** contains information on the neighborhoods of New York City. This is a collection of JSON objects, where each object contains information for one of the city's neighborhoods. Let's take a look at the first examples of the collection:

```javascript
[
    {
        "boro_name":"Queens",
        "name":"St. Albans",
        "shape_area":77412747.8470000029,
        "nta":"QN08",
        "population":48593
    },
    {
        "boro_name":"Bronx",
        "name":"Van Cortlandt Village",
        "shape_area":25666124.5947999991,
        "nta":"BX28",
        "population":50100
    },
    ...
]
```

Each of the JSON objects has the following information:

|Attribute|Description|Domain|
| --- | --- | --- |
| *nta* | ID code of the neighborhood | String |
| *boro_name* | Name of the borough where the neighborhood is located | String |
| *borough_name* | Name of the borough | String |
| *shape_area* | Area units of the neighborhood | Float |
| *population* | Population of the neighborhood | Integer |



The **estaciones.json** file contains information about the possible infrastructures that can be used as stations for fire vehicles. It is a collection of JSON objects, where each object contains information about one of the possible stations. Let's take a look at the first examples of the collection:

```javascript
[
    {
        "address":"42 South Street",
        "capacity":2
    },
    {
        "address":"49 Beekman Street",
        "capacity":1
    },
    {
        "address":"100 Duane Street",
        "capacity":4
    },
    ...
]
```

Each of the JSON objects has the following information:

|Attribute|Description|Domain|
| --- | --- | --- |
| *address* | Station address, acts as an ID | String |
| *capacity* | Vehicles that can be parked simultaneously at the station | Integer |


The **distancias_estaciones.json** file contains information about the distances, in seconds, from each possible station to the rest of the stations. It is a single JSON object containing all the information. The keys are the source station identifiers. The associated values are new JSON objects containing as a key the destination station and the travel time between that origin and destination in seconds as the value.Let's take a look at the first examples of the object:

```javascript
{
    "42 South Street": {
        "49 Beekman Street": 154.94,
        "100 Duane Street": 299.43,
        "14 N. Moore Street": 408.12,
        "75 Canal Street": 296.75,
        "25 Pitt Street": 392.35,
        "222 East 2 Street": 505.01,
        "340 East 14 Street": 600.54,
        "253 Lafayette Street": 408.56,
        "42 Great Jones Street": 494.1,
        ...
    },
    "49 Beekman Street": {
        "42 South Street": 228.56,
        "100 Duane Street": 180.79,
        "14 N. Moore Street": 289.48,
        "75 Canal Street": 295.7,
        ...
    },
    ...
}
```

For example, the travel time between *42 South Street* and *253 Lafayette Street* is 408.56 seconds, and the travel time between *49 Beekman Street* and *42 South Street* is 228.56 seconds.

The **distancias_estaciones_barrios.json** file contains information on the distances, in seconds, from each possible station to the **centroid** of each of the city's neighborhoods. It is a single JSON object that contains all the information. The keys are the source station identifiers. The associated values are new JSON objects containing as a key the neighborhood identifier and as a value the travel time between that origin and destination in seconds.Let's take a look at the first examples of the object:

```javascript
{
    "42 South Street": {
        "QN08": 2123.18,
        "BX28": 1894.39,
        "QN55": 1872.67,
        "BK50": 1532.61,
        "BX41": 1774.19,
        ...
    },
    "49 Beekman Street": {
        "QN08": 2130.2,
        "BX28": 1874.63,
        "QN55": 1776.72,
        "BK50": 1587.44,
        ...
    },
    ...
}
```

For example, the travel time between *42 South Street* and the centroid of *QN55* is 1872.67 seconds, and the travel time between *49 Beekman Street* and *BK50* is 1587.44 seconds.

The last one is the file **incidents2019.json**, which contains a sample of 100000 emergency calls covered by firefighters in 2019. It is a collection of JSON objects, where each object represents an incident. Let's take a look at the first examples of the collection.

```javascript
[
    {
        "nta":"MN03",
        "units":[
            "ladder"
        ],
        "incident_duration":779.0,
        "is_first_shift":true
    },
    {
        "nta":"MN23",
        "units":[
            "engine"
        ],
        "incident_duration":1935.0,
        "is_first_shift":true
    },
    {
        "nta":"BX09",
        "units":[
            "ladder",
            "engine",
            "ladder",
            "ladder"
        ],
        "incident_duration":1127.0,
        "is_first_shift":false
    },
    ...
]
```
Each JSON object has the following information:

|Attribute|Description|Domain|
| ---    | ---       | ---   |
| *nta* | ID of the neighborhood where the incident occurred | String |
| *units* | Vehicles dispatched for the emergency. Possible values are <br>  *engine*, *ladder*, *squad*, *rescue* y *hazardous* | Array of strings |
|*incident_duration* | Duration of incident in seconds | Float |
| *is_first_shift* | Whether or not the incident occurred during the night shift | Boolean |

The following code snippet imports the databases.


In [ ]:
!pip install ortools
from ortools.linear_solver import pywraplp
import json
import requests

response = requests.get("https://gitlab.com/drvicsana/cop-proyecto-2023/-/raw/main/project_data/incidentes2019.json")
incidents_db = json.loads(response.text)

response = requests.get("https://gitlab.com/drvicsana/cop-proyecto-2023/-/raw/main/project_data/distancias_estaciones_barrios.json")
distances_stations_ntas_db = json.loads(response.text)

response = requests.get("https://gitlab.com/drvicsana/cop-proyecto-2023/-/raw/main/project_data/distancias_estaciones.json")
distances_stations_db = json.loads(response.text)

response = requests.get("https://gitlab.com/drvicsana/cop-proyecto-2023/-/raw/main/project_data/barrios.json")
ntas_db = json.loads(response.text)

response = requests.get("https://gitlab.com/drvicsana/cop-proyecto-2023/-/raw/main/project_data/estaciones.json")
stations_db = json.loads(response.text)


# Objectives and phases of the project

The objective of the project is the following: To construct an integer linear optimization model that optimizes the use of resources of the New York City Fire Department.

The first part of the project consists of qualitatively and quantitatively analyzing the data provided to you to determine how the department's resources could be distributed. We highly encourage you to carry out a exploratory data analysis to familiarize yourself with the problem at hand. Once analyzed, you will proceed to the formal modeling of an optimization problem to distribute available resources and the service provided by the department.

The second part of the project consists of programming and solving the optimization problem. The tool to be used for this part is ORTools, as we studied in the laboratory sessions of the course.

Do not worry, as you will not be alone in this project. You and up to 4 other colleagues (5 members) will form a team for both parts of the project.

## Submission requirements

As mentioned above, the project is divided into two phases: a first phase of analysis and formal modeling of the problem, and a second phase of development and solving of the problem itself. In this section we define the requirements of the project, as well as its assessment rubric.

An **article** should be submitted in PDF format with a maximum length of **8 pages**, using the IEEE template available at [following link](https://www.ieee.org/content/dam/ieee-org/ieee/web/org/conferences/conference-template-a4.docx). Stick to the template format as much as possible. The language of the submission is **English**. The sections that should appear (at least) in the article are:
* Abstract: This section describes between 150 and 250 words the model proposed, the main highlights of the project, as well as the results obtained in the experiments carried out.
* Introduction: This section briefly explains the problem to be solved, the importance of this problem for the organization, and the type of techniques to be used for its resolution. Finally, it should describe how the article is organized in sections.
* Related work: 1 academic paper/article related to the application of mathematical programming to similar problems should be reviewed per member. The review will be carried out at a high level, describing the problem to be solved, the type of technique used to solve it, the experiments carried out, and the differences and similarities with the model proposed in your project. The works should appear properly cited in the text, as well as in the bibliography of the article using the format proposed in the template. Maximum length of **1 page**. **An annex should be included identifying who reviewed each article**.
* Proposed optimization model: The mathematical optimization model should be described as it has been done in lectures. That is, using both mathematical notation and natural language. Specifically, the following elements should be defined:
    * Decision variables: Their symbol, their description in natural language, as well as the nature (e.g., integer, binary, real) and domain of the variable (e.g., non-negative) must be defined.
    * Constants: In case of using constants or mathematical notation to define some coefficients or input data of the model, these should also be specified. Specifically, the symbol associated to each constant should be specified, as well as an explanation in natural language of the meaning of such constant.
    * Constraints: For each constraint or family of constraints, a name shall be assigned to identify it, an explanation shall be given in natural language of what the constraint is intended to accomplish, and the mathematical definition of the constraint shall be included. If a family of constraints is defined, it is important to define the corresponding subscripts and indicate the range of the subscripts when generating all the constraints of that family.
    * Objective function: The sense of the optimization (minimize or maximize) as well as the definition of the mathematical function to be optimized should be defined. In addition, an explanation in natural language should be included to explain what is calculated with the proposed objective function and how this calculation is carried out.

* Implementation: The code should be submitted in a separate file to the article. All should be included in a zip file. In the article, you should describe the code developed for the project, as well as its organization. The parts of the code where the variables (which ones and type), the constraints (which ones and what function they have), and the objective function are defined, as well as any other relevant implementation details, should be pointed out and explained.
* Experiments: First you should describe what the objective of the experiments is. After you should describe the set of experiments designed. A set of experiments should be carried out to evaluate the temporal scalability of the model with different solvers (e.g., GLOP, SCIP, CBC). The conclusions of the experiments should be supported by statistical significance tests.
* Conclusions: Summarize the problem solved, the model proposed, the experiments performed, and the conclusions drawn from them. Discuss prospective improvements on your model, as well as on the experiments carried out.
* References: References used in the article to any external resource that has been cited.

**ASSESSMENT RUBRIC**

Next, we attach the assessment rubric for the project. It should be highlighted that the rubric is **approximate**, as it is **IMPOSSIBLE** to identify all prospective scenarios and cases in an open project beforehand.

| Aspect                                       | <50%                                                                                                                                                                                      | 50-69%                                                                                                                                                                                                                  | 70-89%                                                                                                                                                                                                                        | 90-100%                                                                                                                                                                                               |
|-----------------------------------------------|-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| Style, organization and clarity<br>(1 mark)  | The document is not<br> organized in the proposed sections<br><br><br>There is no coherence in<br> ideas and explanations<br><br>References are not present. | There is a certain coherence<br> in ideas and explanations<br><br><br><br>Missing sections<br> or inadequate organization               | There is a certain coherence<br> in ideas and explanation <br><br><br>No missing sections<br><br> Adequate use of figures and tables                        | Ideas and explanations<br> are coherent<br><br>No missing sections <br><br> Adequate use of figures and tables        |
| Related work <br>(1 mark) | No discussion or it is <br> incoherent | 1 article is described adequately | 3 articles are described adequately  | 4-5 articles described adequately  |
| Model<br>(3 marks)                 | No formal model<br> or plagued with errors<br> No significant original ideas or copied                                                                             | Correct and complete<br> definition of two::<br>Variables<br>Constraints<br>Objective function<br><br>The model illustrates<br> insights extracted from the dataset<br><br>The model has some significant original ideas | Correct and complete<br> definition of all elements<br><br>The model incorporates<br> insights extracted from the dataset<br><br> The model has mostly original aspects and ideas | Correct and complete<br> definition of all elements<br><br>The model is truthful to<br> requirements and insights from data<br><br> The model is completely original                   |
| Coding  (3 marks) | Incomplete code, non-functional,<br> no merit or plagiarismo | The code implements part of the model<br>and has merit <br><br> Code partially explained in report | The code implements the model<br> and has merit<br><br> Code explained in report | The code implements the model<br> and has merit<br><br> Code explained in report <br><br>Documented code |
| Experiments <br> (2 marks) | No experiments, no merit,<br> or non-functional | Provided functional code for<br>experiments | Provided functional code for<br>experiments<br><br> Experimental results explained in report | Provided functional code for<br>experiments<br><br> Experimental results explained in report <br><br>Correct methodology for analysis |